In [1]:
import os
import numpy as np
import pandas as pd
import json

# Extract and syncronize data 
it extact data from each trial and save it to 
    /dataset/labeledData/

In [2]:
class make_folder_dataset:
    def __init__(self, folder_path:str,save_path) -> None:
        self.path = folder_path
        self.save_path = save_path
        #os.makedirs(self.save_path)
        self.num_lines_per_message = 130
        self.df = pd.DataFrame()
        self.df_dataset = pd.DataFrame()
        self.tau = ['tau_J0','tau_J1', 'tau_J2', 'tau_J3', 'tau_J4', 'tau_J5', 'tau_J6']
        self.tau_d = ['tau_J_d0','tau_J_d1', 'tau_J_d2', 'tau_J_d3', 'tau_J_d4', 'tau_J_d5', 'tau_J_d6']
        self.tau_ext =['tau_ext0','tau_ext1','tau_ext2','tau_ext3','tau_ext4','tau_ext5','tau_ext6']

        self.q = ['q0','q1','q2','q3','q4','q5','q6']
        self.q_d = ['q_d0','q_d1','q_d2','q_d3','q_d4','q_d5','q_d6']

        self.dq = ['dq0','dq1','dq2','dq3','dq4','dq5','dq6']
        self.dq_d = ['dq_d0','dq_d1','dq_d2','dq_d3','dq_d4','dq_d5','dq_d6']


        self.e = ['e0','e1','e2','e3','e4','e5','e6']
        self.de = ['de0','de1','de2','de3','de4','de5','de6']
        self.etau = ['etau_J0','etau_J1', 'etau_J2', 'etau_J3', 'etau_J4', 'etau_J5', 'etau_J6']
    
    def _extract_array(self, data_dict:dict, data_frame:str, header:list,  n:int):
            dof = 7
            x, y = data_frame[n].split(':')
            y = y.replace('[','')
            y = y.replace(']','')
            y = y.replace('\n','')

            y = y.split(',')
            for i in range(dof):
                data_dict[header[i]].append(float(y[i]))

    def extract_robot_data(self):
        # it extracts robot data from all_data.txt
        f = open(self.path +'/'+ 'all_data.txt', 'r')
        lines = f.readlines()

        keywords = ['time'] + self.tau + self.tau_d + self.tau_ext + self.q + self.q_d + self.dq + self.dq_d 

        data_dict = dict.fromkeys(keywords)
        for i in keywords:
            data_dict[i]=[0]
        
        for i in range(int(len(lines)/self.num_lines_per_message)):
            data_frame = lines[i*self.num_lines_per_message:(i+1)*self.num_lines_per_message]
            
            x, y = data_frame[3].split(':')
            time_ = int(y)-int(int(y)/1000000)*1000000

            x, y = data_frame[4].split(':')
            time_ = time_+int(y)/np.power(10,9)

            data_dict['time'].append(time_)
            
            self._extract_array(data_dict,data_frame,self.tau, 25)
            self._extract_array(data_dict,data_frame,self.tau_d, 26)
            self._extract_array(data_dict,data_frame, self.tau_ext, 37)
            
            self._extract_array(data_dict,data_frame,self.q, 28)
            
            self._extract_array(data_dict,data_frame, self.q_d, 29)
            self._extract_array(data_dict,data_frame, self.dq, 30)
            self._extract_array(data_dict,data_frame, self.dq_d, 31)
        
       
        self.df = pd.DataFrame.from_dict(data_dict)
        self.df = self.df.drop(index=0).reset_index()
        
        for i in range(len(self.e)):
            self.df[self.e[i]] = self.df[self.q_d[i]]-self.df[self.q[i]]
        for i in range(len(self.de)):
            self.df[self.de[i]] = self.df[self.dq_d[i]]-self.df[self.dq[i]]
        for i in range(len(self.etau)):
            self.df[self.etau[i]] = self.df[self.tau_d[i]]-self.df[self.tau[i]]

        # Add 'label' column and initialize to 0
        # self.df['label'] = 0

         # Print the DataFrame after extraction to verify content
        # print("DataFrame after extraction:")
        # print(self.df.head())

        #self.df.to_csv(self.save_path +'robot_data.csv',index=False)
        
    def get_labels(self):
        # Load the true labeled (contact- noncontact) data
        true_label_path = os.path.join(self.path, 'true_label.csv')
        
        # Initialize DataFrame for labels
        self.df['label'] = 0
        
        # Check if true_label.csv exists and is not empty
        if not os.path.exists(true_label_path) or os.stat(true_label_path).st_size == 0:
            print(f"Warning: Empty or missing true_label.csv in {self.path}. All labels set to 0.")
        else:
            true_label = pd.read_csv(true_label_path)
            
            # Check if true_label is empty after loading
            if true_label.empty:
                print(f"Warning: true_label.csv is empty. All labels set to 0.")
            else:
                # Adjust time column in true_label
                true_label['time'] = true_label['time_sec'] + true_label['time_nsec'] - self.df['time'][0]
                
                # Compute the time difference and determine contact events
                time_dev = true_label['time'].diff()
                contact_events_index = np.append([0], true_label['time'][time_dev > 0.05].index.values)
                contact_events_index = np.append(contact_events_index, true_label['time'].shape[0] - 1)

                # Check if contact_events_index is empty
                if len(contact_events_index) == 0:
                    print(f"Warning: No contact events found in {true_label_path}. All labels set to 0.")
                else:
                    self.df['time'] = self.df['time'] - self.df['time'][0]
                    contact_count = 0
                    self.df['label'] = 0

                    for i in range(self.df['time'].shape[0]):
                        if contact_count >= len(contact_events_index):
                            break
                        if (self.df['time'][i] - true_label['time'][contact_events_index[contact_count]]) > 0:
                            contact_count += 1
                            if contact_count >= len(contact_events_index):
                                break
                            for j in range(i, self.df['time'].shape[0]):
                                self.df.loc[j, 'label'] = 1
                                if contact_count >= len(contact_events_index) or \
                                (self.df['time'][j] - true_label['time'][contact_events_index[contact_count] - 1]) > 0:
                                    i = j
                                    break

        # Print the DataFrame before saving to verify content
        # print("DataFrame before saving:")
        # print(self.df.head())
        
        # Save the labeled data
        output_file = os.path.join(self.save_path, 'labeled_data.csv')
        self.df.to_csv(output_file, index=False)
        print(f"labeled_data.csv saved to {output_file}")
   
    

    # def get_labels(self):
    #     # it syncronize true labeled (contact- noncontact) data with robot data
    #     true_label = pd.read_csv(self.path +'/'+'true_label.csv')
    #     true_label['time'] = true_label['time_sec']+true_label['time_nsec']-self.df['time'][0]
    #     time_dev = true_label['time'].diff()
    #     contact_events_index = np.append([0], true_label['time'][time_dev>0.05].index.values)
    #     contact_events_index = np.append(contact_events_index,  true_label['time'].shape[0]-1)

    #     self.df['time'] = self.df['time'] - self.df['time'][0]
    #     contact_count = 0
    #     self.df['label']=0

    #     for i in range(self.df['time'].shape[0]):
    #         if (self.df['time'][i]-true_label['time'][contact_events_index[contact_count]]) > 0:
    #             #print(i ,',', contact_events_index[contact_count], ',',self.df['time'][i], '   ', true_label['time'][contact_events_index[contact_count]] )
    #             contact_count += 1
    #             if contact_count == len(contact_events_index):
    #                 break
    #             for j in range(i, self.df['time'].shape[0]):
    #                 self.df.loc[j, 'label'] = 1
    #                 #print(j)
    #                 if (self.df['time'][j] - true_label['time'][contact_events_index[contact_count]-1]) > 0:
    #                     #print(j ,',', contact_events_index[contact_count]-1, ',', self.df['time'][j], '   ', true_label['time'][contact_events_index[contact_count]-1] )
    #                     #print('----------------------------------------')
    #                     i = j
    #                     break
    #     self.df.to_csv(os.path.join(self.save_path,'labeled_data.csv'), index=False)


    # def make_sequence(self):
    #     #window_time = 140ms
    #     seq_num = 28
    #     gap = 4
    #     selected_features= self.e + self.tau

    #     dataset = pd.DataFrame(np.ones((int((self.df.shape[0]-seq_num)/gap), seq_num*len(selected_features)+1))*2 )
    #     index = 0
    #     state = False
    #     last_contact_indexes = self.df.loc[self.df['label']==1,'index'].values
    #     last_contact_indexes = last_contact_indexes[last_contact_indexes.shape[0]-1]

    #     for i in range(0, last_contact_indexes, gap):
    #         if state: 
    #             window = self.df[selected_features][i:i+seq_num]
    #             dataset.iloc[index,0] = self.df['label'][i+seq_num]
    #             dataset.iloc[index, 1:len(dataset.columns)] = np.hstack(window.to_numpy())
    #             index += 1
    #         else:
    #             if self.df['label'][i+seq_num] == 1:
    #                 state = 1
    #     self.dataset = dataset.drop(index=dataset.loc[dataset[0]==2,0].index)


    #     sequence_data_path = os.path.join(self.save_path, 'sequence')
    #     os.makedirs(sequence_data_path, exist_ok=True)

    #     name = self.path.split('/')[-1] + '_sequence.csv'
    #     self.dataset.to_csv(os.path.join(sequence_data_path, name), index=False)

    #     """ name = self.path.split('/')[len(self.path.split('/'))-2]+'.csv'
    #     self.dataset.to_csv(self.save_path+name, index=False) """
    #     return self.dataset
    
    # def split_data(self, train_split_rate = 0.75):
    #     msk = np.random.rand(len(self.dataset)) < train_split_rate
    #     train = self.dataset.loc[msk, :]
    #     test = self.dataset.loc[~msk, :]

    #     test_train_data_path = os.path.join(self.save_path, 'test_train')
    #     os.makedirs(test_train_data_path, exist_ok=True)
        
    #     name = self.path.split('/')[-1] + '_train.csv'
    #     train.to_csv(os.path.join(test_train_data_path, name), index=False)
    #     name = self.path.split('/')[-1] + '_test.csv'
    #     test.to_csv(os.path.join(test_train_data_path, name), index=False)


In [306]:
import os
import shutil
data_path = '../DATA/'

# Specify the directory you want to list files for
robot_data_path = data_path + 'rawData/'
dataset_path = os.path.join(data_path,'Labeled_data/')

if os.path.exists(dataset_path):
    shutil.rmtree(dataset_path)
os.makedirs(dataset_path,exist_ok=True)

# # Get a list of all files and directories in the specified directory
# files_and_dirs = [f for f in os.listdir(robot_data_path) if f != 'Labeled_data']
# #print(files_and_dirs)

# Get a list of all directories in the specified directory, excluding .DS_Store
files_and_dirs = [f for f in os.listdir(robot_data_path) if os.path.isdir(os.path.join(robot_data_path, f)) and f != '.DS_Store']


for folder_name in files_and_dirs:
    print(f"folder_name {folder_name}")
    folder_path = robot_data_path + folder_name
    save_data_file = dataset_path + folder_name 
    #print(f" save_data_file is {save_data_file}")
    #os.makedirs(save_data_file, exist_ok=True)
    os.makedirs(save_data_file,exist_ok= True)
    instance = make_folder_dataset(folder_path,save_data_file)
    instance.extract_robot_data()
    instance.get_labels() 

    # instance.make_sequence()
    # instance.split_data()
    
instance.df.head()


folder_name 0204-7ST-3F4
labeled_data.csv saved to ../DATA/Labeled_data/0204-7ST-3F4/labeled_data.csv
folder_name 0204-7ST-3R1
labeled_data.csv saved to ../DATA/Labeled_data/0204-7ST-3R1/labeled_data.csv
folder_name 0204-7DT-3R1
labeled_data.csv saved to ../DATA/Labeled_data/0204-7DT-3R1/labeled_data.csv
folder_name 0204-7P-3F1
labeled_data.csv saved to ../DATA/Labeled_data/0204-7P-3F1/labeled_data.csv
folder_name 0204-7ST-3R4
labeled_data.csv saved to ../DATA/Labeled_data/0204-7ST-3R4/labeled_data.csv
folder_name 0204-7ST-3U4
labeled_data.csv saved to ../DATA/Labeled_data/0204-7ST-3U4/labeled_data.csv
folder_name 0204-7P-3L1
labeled_data.csv saved to ../DATA/Labeled_data/0204-7P-3L1/labeled_data.csv
folder_name 0204-7P-3U1
labeled_data.csv saved to ../DATA/Labeled_data/0204-7P-3U1/labeled_data.csv
folder_name 0204-7DT-3R2
labeled_data.csv saved to ../DATA/Labeled_data/0204-7DT-3R2/labeled_data.csv
folder_name 0204-7G-3B1
labeled_data.csv saved to ../DATA/Labeled_data/0204-7G-3B1/label

index      time    tau_J0     tau_J1    tau_J2     tau_J3    tau_J4  \
0      1  0.000000 -0.339380 -47.617908  1.917226  19.081491  0.308860   
1      2  0.005002 -0.339380 -47.617908  1.917226  19.081491  0.308860   
2      3  0.010010 -0.264001 -47.732960  1.952932  19.045786  0.299705   
3      4  0.015012 -0.264001 -47.732960  1.952932  19.045786  0.299705   
4      5  0.019995 -0.299707 -47.732960  1.952932  19.045786  0.299705   

     tau_J5    tau_J6  tau_J_d0  ...       de5       de6   etau_J0    etau_J1  \
0  2.184338  0.021839       0.0  ... -0.000151  0.002979  0.339380  47.617908   
1  2.184338  0.021839       0.0  ... -0.000151  0.002979  0.339380  47.617908   
2  2.195324  0.011769       0.0  ...  0.000216  0.002506  0.264001  47.732960   
3  2.195324  0.011769       0.0  ...  0.000216  0.002506  0.264001  47.732960   
4  2.195324 -0.008373       0.0  ...  0.000259  0.001726  0.299707  47.732960   

    etau_J2    etau_J3   etau_J4   etau_J5   etau_J6  label  
0 -1.917226 -19.081491 -0.308860 -2.184338 -0.021839      0  
1 -1.917226 -19.081491 -0.308860 -2.184338 -0.021839      0  
2 -1.952932 -19.045786 -0.299705 -2.195324 -0.011769      0  
3 -1.952932 -19.045786 -0.299705 -2.195324 -0.011769      0  
4 -1.952932 -19.045786 -0.299705 -2.195324  0.008373      0  

[5 rows x 73 columns]

# plot data

In [3]:
import chart_studio.plotly as py
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode
# Using plotly + cufflinks in offline mode
import cufflinks
cufflinks.go_offline(connected=True)
init_notebook_mode(connected=True)

In [7]:
import os
data_path = '../DATA/'

# Specify the directory you want to list files for

robot_data_path = data_path + 'ModelData/'
print(f"robot_data_path {robot_data_path}")
dataset_path = os.path.join(data_path,'Labeled_data/')
print(f"dataset_path {dataset_path}")

# robot_data_path = data_path
label_data_path = data_path
# dataset_path = data_path+'Labeled_data/'
# os.makedirs(dataset_path, exist_ok=True)

# Get a list of all files and directories in the specified directory
files_and_dirs = os.listdir(dataset_path)

# files_and_dirs = ['0910-test2']
# files_and_dirs = ['link6SingleTapHead']
files_and_dirs = ['0214_2LCNN_Post123_T5_ST']
# '0910-7STR-Y1':30 times, some have low peak value but the majority are normal peak value
# '0910-7STL-Y1':30 times, last one contact label shorter than real contact time
# '0910-7STB-S1': 30 times, 21 contact label too shorter than real contact time

print(f"files_and_dirs is {files_and_dirs}")
for folder_name in files_and_dirs:
    print(f"folder_name is {folder_name}")
    folder_path = robot_data_path + folder_name
    print(f"folder_path is {folder_path}")
    
save_data_file = dataset_path + folder_name
print(f"save_data_file is {save_data_file}")
os.makedirs(save_data_file, exist_ok=True)    
data = make_folder_dataset(folder_path,save_data_file)
data.extract_robot_data()
data.get_labels()
data.df.iplot(x='time', y=['label'])
data.df['label2'] = data.df['label'] * 10
targetA = data.tau_ext
# targetB = data.q_d

data.df.iplot(x='time', y = targetA+ ['label2'], xTitle='time (sec)')
data.df.iplot(x='time', y = 'label', xTitle='time (sec)')
# break

robot_data_path ../DATA/ModelData/
dataset_path ../DATA/Labeled_data/
files_and_dirs is ['0214_2LCNN_Post123_T5_ST']
folder_name is 0214_2LCNN_Post123_T5_ST
folder_path is ../DATA/ModelData/0214_2LCNN_Post123_T5_ST
save_data_file is ../DATA/Labeled_data/0214_2LCNN_Post123_T5_ST
labeled_data.csv saved to ../DATA/Labeled_data/0214_2LCNN_Post123_T5_ST/labeled_data.csv


In [7]:
target = ['e1','tau_J1']

for i in target:
    A = instance.df[i].max()-instance.df[i].min()
    instance.df['label_scaled']=instance.df['label']*A + instance.df[i][0] -A/2
    instance.df.iplot(x='time', y= [i, 'label_scaled'], xTitle='time (sec)', yTitle=i)
    
    #plt.plot(instance.df['time'],instance.df['labeled_scaled'])
    

KeyError: 'e1'

In [55]:
df_master_master_train[0][df_master_master_train[0]==1]
target = ['e0','tau_J0']

for i in target:
    A = instance.df[i].max()-instance.df[i].min()
    instance.df['label_scaled']=instance.df['label']*A + instance.df[i][0] -A/2
    instance.df.iplot(x='time', y= [i, 'label_scaled'], xTitle='time (sec)', yTitle)

SyntaxError: positional argument follows keyword argument (2842084700.py, line 7)

In [ ]:
df_master_master_train[0][df_master_master_train[0]==1]

# Make Dataset


## Features

In [80]:
tau = ['tau_J0','tau_J1', 'tau_J2', 'tau_J3', 'tau_J4', 'tau_J5', 'tau_J6']
tau_d = ['tau_J_d0','tau_J_d1', 'tau_J_d2', 'tau_J_d3', 'tau_J_d4', 'tau_J_d5', 'tau_J_d6']
tau_ext =['tau_ext0','tau_ext1','tau_ext2','tau_ext3','tau_ext4','tau_ext5','tau_ext6']

q = ['q0','q1','q2','q3','q4','q5','q6']
q_d = ['q_d0','q_d1','q_d2','q_d3','q_d4','q_d5','q_d6']

dq = ['dq0','dq1','dq2','dq3','dq4','dq5','dq6']
dq_d = ['dq_d0','dq_d1','dq_d2','dq_d3','dq_d4','dq_d5','dq_d6']


e = ['e0','e1','e2','e3','e4','e5','e6']
de = ['de0','de1','de2','de3','de4','de5','de6']
etau = ['etau_J0','etau_J1', 'etau_J2', 'etau_J3', 'etau_J4', 'etau_J5', 'etau_J6']

## required functions

In [81]:
import numpy as np
import pandas as pd


def split_data(dataset, train_split_rate = 0.75):
    msk = np.random.rand(len(dataset)) < train_split_rate
    train = dataset.loc[msk, :]
    test = dataset.loc[~msk, :]
    return train, test

def make_sequence(df, selected_features, seq_num = 28, gap = 4):
    dataset = pd.DataFrame(np.ones((int((df.shape[0]-seq_num)/gap), seq_num*len(selected_features)+1))*2 )
    index = 0
    state = False
    last_contact_indexes = df.loc[df['label']==1,'index'].values
    last_contact_indexes = last_contact_indexes[last_contact_indexes.shape[0]-1]

    for i in range(0, last_contact_indexes, gap):
        if state: 
            window =df[selected_features][i:i+seq_num]
            dataset.iloc[index,0] = df['label'][i+seq_num]
            dataset.iloc[index, 1:len(dataset.columns)] = np.hstack(window.to_numpy())
            index += 1
        else:
            if df['label'][i+seq_num] == 1:
                state = 1
    dataset = dataset.drop(index=dataset.loc[dataset[0]==2,0].index)
    return dataset

def make_sequence_full_time(df, selected_features, seq_num = 28, gap = 4):
    dataset = pd.DataFrame(np.ones((int((df.shape[0]-seq_num)), seq_num*len(selected_features)+1))*2 )
    index = 0
    last_contact_indexes = df.loc[df['label']==1,'index'].values
    last_contact_indexes = last_contact_indexes[last_contact_indexes.shape[0]-1]

    for i in range(0, df.shape[0]-seq_num-1, gap):

        window =df[selected_features][i:i+seq_num]
        dataset.iloc[index,0] = df['label'][i+seq_num]
        dataset.iloc[index, 1:len(dataset.columns)] = np.hstack(window.to_numpy())
        index += 1

    dataset = dataset.drop(index=dataset.loc[dataset[0]==2,0].index)
    return dataset

## make a dataset with a set of features


In [83]:
import os


saveDatasetPath= "../DATA/output/"
labeledDataPath = "../DATA/Labeled_data/"


train_split_rate = 0.7

selected_features = tau + tau_ext + e + de
seq_num = 28

dict_label = {'a': 7, 'b':6, 'c':5, 'd':4, 'e':3, 'f':2, 'g':1}
columns = range(seq_num*len(selected_features)+1)

df_master_master_train = pd.DataFrame(columns=columns)
df_master_master_test = pd.DataFrame(columns=columns)

    
for i in os.listdir(labeledDataPath):
    if len(i.split('.'))==1:

        df_master_train = pd.DataFrame(columns=columns)
        df_master_test = pd.DataFrame(columns=columns)

        submain_path = labeledDataPath+i+'/'
        print(submain_path)
        for tag_name in os.listdir(submain_path):
            if len(tag_name.split('.'))==1:
                file_path = submain_path+tag_name+'/labeled_data.csv'
                df = pd.read_csv(file_path)
                df = make_sequence_full_time(df, selected_features,seq_num)
                #labeling data
                df[0] = df[0]*dict_label[tag_name[0]]
                train, test = split_data(df, train_split_rate)
                df_master_train = df_master_train.append(train, ignore_index=True)
                df_master_test = df_master_test.append(test, ignore_index=True)
                
        df_master_train.to_pickle(saveDatasetPath+i+'_train.pkl')
        df_master_test.to_pickle(saveDatasetPath+i+'_test.pkl')
        
    df_master_master_train = df_master_master_train.append(df_master_train, ignore_index=True)
    df_master_master_test = df_master_master_test.append(df_master_test, ignore_index=True)

df_master_master_train.to_pickle(saveDatasetPath+'dataset_train.pkl')
df_master_master_test.to_pickle(saveDatasetPath+'dataset_test.pkl')
 

../DATA/Labeled_data/0724-7ST-Y1/


FileNotFoundError: [Errno 2] No such file or directory: '../DATA/Labeled_data/0724-7ST-Y1/sequence/labeled_data.csv'

# # Print Dataset Information

In [61]:
print('number of all samples: ', df_master_master_train.shape[0]+df_master_master_test.shape[0])
print('number of noncontact samples: ', df_master_master_train[0][df_master_master_train[0]==0].shape[0] +  df_master_master_test[0][df_master_master_test[0]==0].shape[0] )
print('number of contact samples: ', df_master_master_train[0][df_master_master_train[0]!=0].shape[0] +  df_master_master_test[0][df_master_master_test[0]!=0].shape[0] )
print('Link1 samples: ', df_master_master_train[0][df_master_master_train[0]==1].shape[0] +  df_master_master_test[0][df_master_master_test[0]==1].shape[0] )
print('Link2 samples: ', df_master_master_train[0][df_master_master_train[0]==2].shape[0] +  df_master_master_test[0][df_master_master_test[0]==2].shape[0] )
print('Link3 samples: ', df_master_master_train[0][df_master_master_train[0]==3].shape[0] +  df_master_master_test[0][df_master_master_test[0]==3].shape[0] )
print('Link4 samples: ', df_master_master_train[0][df_master_master_train[0]==4].shape[0] +  df_master_master_test[0][df_master_master_test[0]==4].shape[0] )
print('Link5 samples: ', df_master_master_train[0][df_master_master_train[0]==5].shape[0] +  df_master_master_test[0][df_master_master_test[0]==5].shape[0] )
print('Link6 samples: ', df_master_master_train[0][df_master_master_train[0]==6].shape[0] +  df_master_master_test[0][df_master_master_test[0]==6].shape[0] )
print('Link7 samples: ', df_master_master_train[0][df_master_master_train[0]==7].shape[0] +  df_master_master_test[0][df_master_master_test[0]==7].shape[0] )

number of all samples:  0
number of noncontact samples:  0
number of contact samples:  0
Link1 samples:  0
Link2 samples:  0
Link3 samples:  0
Link4 samples:  0
Link5 samples:  0
Link6 samples:  0
Link7 samples:  0
